# Fondements du Machine Learning - L3 IM2D, 2020-2021
# TP 1 : Interpolation et régression linéaire

Le polycopié de cours est disponible [ici](https://www.lamsade.dauphine.fr/%7Ecroyer/ensdocs/FML/PolyFML.pdf).

Ce notebook est disponible en ligne via [ce lien](https://www.lamsade.dauphine.fr/~croyer/ensdocs/FML/FML-TP01.ipynb). La correction sera disponible après les séances [ici](https://www.lamsade.dauphine.fr/~croyer/ensdocs/FML/FML-TP01-Correction.ipynb).

Ce TP utilise la librairie *NumPy*. Un tutoriel sur NumPy (en anglais) est disponible [ici](https://sebastianraschka.com/pdf/books/dlb/appendix_f_numpy-intro.pdf).

Pour tout commentaire sur ce notebook, merci d'envoyer un courriel à clement.royer@dauphine.psl.eu.

In [ ]:
# A executer pour demarrer le TP : on importe des packages et fonctions utiles
import numpy as np
from scipy.linalg import norm
from scipy.special import comb
import matplotlib.pyplot as plt

## 0 - Contexte

*Un problème classique en apprentissage est l'interpolation de données via des modèles de complexité croissante.
Cela peut se modéliser par un problème de régression linéaire.*

Dans ce TP, nous allons chercher à estimer les paramètres d'une courbe de Bézier. Une courbe de Bézier est une fonction polynômiale décrite par un ensemble de points de contrôle. On dit que la courbe est de degré $d$ si elle possède $d+1$ points de contrôle.

Pour ce TP, on se place dans le plan, c'est-à-dire que l'on considère $d+1$ points $(\alpha_i,\beta_i) \in (\mathbb{R}^2)^{d+1}$, où les abscisses $\alpha_i=\frac{i}{d}$ sont uniformément réparties sur $[0,1]$, et les ordonnées $\beta_i$ sont choisies dans $\mathbb{R}$. 

Une courbe de Bézier est alors donnée par :
$$
           c: \left\{
               \begin{array}{lll}
                       [0,1] &\rightarrow &\mathbb{R} \\
                       t &\mapsto &y = c(t;\beta_0,\boldsymbol{\beta},\beta_d)
               \end{array}
               \right.
$$
où
* Le vecteur $\boldsymbol{\beta} = [\beta_1,\dots,\beta_{d-1}]^T$ représente les paramètres du modèle à estimer, contrairement aux valeurs $\beta_0$ et $\beta_d$ qui sont supposées connues.
* L'expression $c(t,\beta_0,\boldsymbol{\beta},\beta_d)$ est définie par
$$
    c(t;\beta_0,\boldsymbol{\beta},\beta_d) = \beta_0 B_0^d (t) + \sum_{i=1}^{d-1} \beta_i B_i^d (t) 
    + \beta_d B_d^d (t).
$$
* Les *polynômes de Bernstein* $B_i^d$ sont définis pour $i=0,\dots,d$ par $B_i^d(t) = C_i^d t^i (1-t)^{d-i}$, avec 
$C_i^d$ le nombre de combinaisons de $i$ objets parmi $d$ (on utilisera la fonction **comb** pour le calculer).

*Remarque : avec cette définition, on a*
$$ 
    \left\{ 
        \begin{array}{l}
            c(\alpha_0;\beta_0,\boldsymbol{\beta},\beta_d) = c(0;\beta_0,\boldsymbol{\beta},\beta_d) = \beta_0, \\
            c(\alpha_d;\beta_0,\boldsymbol{\beta},\beta_d) = c(1;\beta_0,\boldsymbol{\beta},\beta_d) = \beta_d.
        \end{array}
    \right.
$$

*La courbe inclut donc les points $(\alpha_0,\beta_0)$ et $(\alpha_d,\beta_d)$ (mais aucun des autres points de contrôle). Cela justifie que l'on se concentre sur l'estimation des $\beta_i$ restants.*

Les courbes de Bézier peuvent être utilisés pour interpoler des données : cependant, plus le degré d'une courbe est élevé, plus elle représente un modèle complexe des données, qui peut être trop attaché aux données (on parle ainsi d'*overfitting* en apprentissage). Le but de ce TP est d'illustrer ce phénomène, en mettant à profit les éléments du cours liés à la régression linéaire.


## 1 - Production des données

On souhaite générer des données d'une courbe de Bézier et leur appliquer un bruit gaussien (distribué selon une loi normale). Pour ce faire, on commence par écrire une fonction représentant la courbe de Bézier.


* Compléter le code ci-dessous pour calculer les valeurs d'une courbe de Bézier. Ce code doit fonctionner avec une ou plusieurs valeurs d'abscisses, et pour toute valeur de $d \ge 1$.

In [ ]:
# Code pour le calcul d'ordonnees d'une courbe de Bezier dans le plan
def bezier(t,d,beta_0,beta,beta_d):
    '''
        Calcul d'une courbe de Bézier dans le plan en une ou plusieurs abscisses.
        
        Entrees :
            t : tableau NumPy unidimensionnel, ou reel
            d : degre de la courbe de Bezier recherchee
            beta_0 : parametre de la courbe correspondant au polynome de Bernstein d'indice 0
            beta : parametres de la courbe correspondant aux polynomes de Bernstein d'indices 1 a d-1 (optionnel si d=1)
            beta_d : parametres de la courbe correspondant au polynome de Bernstein d'indice d
        
        Sorties :
            c : tableau NumPy unidimensionnel, ou reel correspondant aux valeurs de la courbe
    '''

    # Debut code a completer

    # Fin code a completer

### 1.2 Génération du jeu de données

Etant donnés un jeu de paramètres, on peut utiliser la fonction ci-dessus pour tirer un nombre arbitraire de points.

On se donne donc une paramétrisation de la courbe, c'est-à-dire un entier $d^*$ et un ensemble d'ordonnées $\beta_0,\beta_1^*,\dots,\beta_{d^*-1}^*,\beta_{d^*}$. On supposera que l'on génère des données bruitées par un bruit gaussien.


* Utiliser le script ci-dessous pour générer $n$ points de la forme $(\alpha_i,\beta_i)_{i=0}^{d^*}$ avec
$$
    y_i = c(\alpha_i;\beta_0,\beta_1^*,\dots,\beta_{d^*-1}^*,\beta_{d^*}) + \epsilon_i, \quad 
    \epsilon_i \sim \mathcal{N}(0,\sigma^2).
$$

In [ ]:
# Validation de l'implémentation
d_star=5
n=40
sigma=0.5
beta_0 = 115
beta_star = np.array([133,96,139,118])
beta_dstar = 123
t = np.linspace(0,1,n)
print(t)
c = bezier(t,d_star,beta_0,beta_star,beta_dstar)
print(c)
eps = np.random.normal(0,sigma,n)
y = c+np.array(eps)

# Representation des donnees et de la courbe de Bezier sous-jacente.
plt.figure()
plt.plot(t,c,label='Curve')
plt.plot(t,y,'o',label='Data')
plt.show()


## 2 - Estimation des paramètres par moindres carrés linéaires

On suppose maintenant que l'on dispose d'un échantillon de $n$ points tirés (avec bruit) selon une courbe de Bézier . On suppose de surcroît que l'on connaît les deux paramètres $\beta_0$ et $\beta_{d^*}$, *mais pas le degré d*. L'ensemble des paramètres inconnus est donc ($\beta_1^*,\dots,\beta_{d^*-1}^*,d^*$). Le problème d'estimation de ces paramètres est linéaire en les coefficients de $\boldsymbol{\beta}^* = (\beta_1^*,\dots,\beta_{d^*-1}^*)^T$, mais non linéaire par rapport au degré $d^*$.

Dans un premier temps, on fait donc une hypothèse sur la valeur de $d^*$, que l'on fixe. On suppose donc que l'on cherche une courbe de Bézier paramétrée par $(\beta_0,\beta_1,\dots,\beta_{d-1},\beta_d=\beta_{d^*})$ et on résout le problème aux moindres carrés suivant :
$$
    \hat{\boldsymbol{\beta}} = \arg\min_{\boldsymbol{\beta} \in \mathbb{R}^{d-1}} 
    \frac{1}{2} \sum_{i=1}^n \left(c(t_i,\beta_0,\boldsymbol{\beta},\beta_{d^*})-y_i\right)^2.
$$

* En posant $\boldsymbol{x}_i=(B_0^d(t_i),B_1^d(t_i),\dots,B_d^d(t_i))^T$, montrer que le problème est bien linéaire en les coefficients de $\boldsymbol{\beta}$. Compléter la fonction ci-dessous qui calcule $X = \left[ \begin{array}{c} x_0^T \\ \vdots \\ x_d^T \end{array} \right] \in \mathbb{R}^{n \times (d+1)}$ à partir des $t_i$.

In [ ]:
def bernstein(t,d):
    '''
        Calcul des coefficients de Bernstein en divers points du plan, pour un degre donne.
        
        Entrees :
            t : tableau NumPy unidimensionnel avec n elements
            d : degre des polynomes de Bernstein a utiliser
        
        Sortie : 
            X : tableau NumPy bidimensionnel contenant les n*(d+1) coefficients
    '''
    
    # Debut du code a completer
 
    # Fin du code a completer
    return X

* Compléter le code ci-dessous pour déterminer la meilleure courbe de Bézier à d fixé. 
    * On pourra faire appel à la fonction **pinv** depuis le package **linalg** de NumPy (que l'on appelle via *np.linalg.pinv*).
    * On fera attention à ne pas optimiser sur $\beta_0$ et $\beta_d$, qui sont supposés connus.

In [ ]:
# Estimation par moindres carres lineaires des coefficients de beta
def estimbeta(X,y,beta_0,beta_d):
    '''
        Estimation des parametres d'une courbe de Bézier dans le plan.
        
        Entrees :
            X : tableau NumPy bidimensionnel avec (d+1) colonnes
                Chaque ligne est la transposee d'un vecteur x_i defini comme ci-dessus.
            y : ordonnees des points echantillons
            beta_0 : parametre de la courbe correspondant au polynome de Bernstein d'indice 0
            beta_d : parametres de la courbe correspondant au polynome de Bernstein d'indice d
        
        Sorties :
            beta : tableau NumPy unidimensionnel correspondant aux polynomes de Bernstein d'indices 1 a d-1 
    '''
    
    # Debut du code a completer
    
    # Fin du code a completer
    
    return beta

On peut donc maintenant calculer des estimations pour $d$ fixé, et regarder si la courbe correspondante interpole bien les points recherchés.

* Tracer la courbe de Bézier apprise sur les données. Tester plusieurs valeurs de $d$. Semble-t-il possible de trouver le degré du modèle exact à partir de ces courbes ?

In [ ]:
# Tracé des points initiaux
plt.figure()
plt.plot(t,y,'o',label='data')

# Tracé de plusieurs courbes de Bezier
dvals = [2,3,4,5,6,7]

for i_d in dvals:
    # Debut code a completer
    #
    # Former la matrice X et calculer l'estimation de beta

    # Tracer la courbe de Bezier correspondant a l'estimation avec le label ci-dessous
    label_est = 'd='+str(i_d)
    
    # Fin code a completer

plt.legend()
plt.show()


## 3 - Erreur d'apprentissage

On définit l'erreur d'apprentissage, ou le risque empirique, comme l'écart entre les données et les prédicitions obtenues.

* Que vaut l'erreur d'apprentissage avec les définitions de la partie 2 ?

* Compléter le script ci-dessous afin de calculer l'erreur d'apprentissage pour $d$ choisi entre 2 et 16, puis tracer la courbe correspondante.

In [ ]:
# Erreur d'apprentissage pour différentes valeurs de d
plt.figure()
dvals = np.arange(2,17) # Valeurs possibles de d
n_dvals = dvals.shape[0]
e = np.zeros(n_dvals) # Vecteur des erreurs

for i_d in range(0,n_dvals):
    # Debut code a completer
    #

    # Former la matrice X et calculer l'estimation de beta

    # Calculer l'erreur d'apprentissage 

    #
    # Fin code a completer

# Afficher l'erreur
plt.semilogy(dvals,e)
plt.show()

## Question complémentaire

On a vu en cours que l'estimateur des moindres carrés est égal à l'estimateur du maximum de vraisemblance en considérant un biais gaussien sur les données. On peut montrer que cet estimateur est asymptotiquement non biaisé, c'est-à-dire qu'il tend à être non biaisé quand le nombre d'échantillons tend vers l'infini.

En utilisant les fonctions des parties 1 et 2, et en supposant que $d^*=5$ est connu, tirer un grand nombre de données d'apprentissage et stocker les différents vecteurs de paramètres estimés selon la procédure de la partie 2. Moyenner ces estimateurs pour vérifier qu'ils convergent vers la valeur originelle.

***Références***

* *V. Charvillat, TP Apprentissage et Applications, INP-ENSEEIHT, 2011-2012.*
* *Il existe bien évidemment une fonction dans Python qui permet de résoudre les problèmes aux moindres carrés, et que l'on aurait pu utiliser ici. Il s'agit de [lstsq](https://docs.scipy.org/doc/scipy/reference/generated/scipy.linalg.lstsq.html) du package* ***scipy.linalg***.